In [1]:
import importlib
import sys
from WikiSpider import WikiSpider
importlib.reload(sys.modules['WikiSpider'])
from bs4 import BeautifulSoup
from selenium import webdriver
from tqdm import tqdm
from nltk.stem.porter import *
from selenium.webdriver.chrome.options import Options
import json 

## Web Crawling: wikipedia
    
includes: raw data!!

museum_list  ->  wikipedia_museum_list.jsonl

museum_articles -> wikipedia_museum_articles.jsnol


In [21]:
spider = WikiSpider()

In [ ]:
state_museums_list = spider.get_states_museums_list()
state_museums_list

given workload (i.e. web crawling), I drop the states whose html cannot be crawled by function (which is fine, only four states are left out)

In [21]:
# edge-case: wikipedia page sucks :), the row that should be in the first row is set as the table titles

Illinois = state_museums_list['Illinois']
old_keys = list(Illinois[0].keys())
new_keys = ['Museum name','Location','County','Region','Area of study','Summary','website']
new_museums_list_Illinois = []
for museum in Illinois:
    new_museum = {}
    for i in range(len(old_keys)):
        try:
            new_museum[new_keys[i]] = museum[old_keys[i]]
        except KeyError:
            new_museum[new_keys[i]] = ['','']
            
    new_museums_list_Illinois.append(new_museum)

In [26]:
state_museums_list['Illinois'] = new_museums_list_Illinois

In [ ]:
file_name = './data_1101/wikipedia_museum_list.jsonl'
spider.wiki_save_raw_list(file_name,state_museums_list)

In [36]:
# edge_case: image is in the first column
name_list = set()
for key,value in state_museums_list.items():
    name = list(value[1].keys())[0]
    if name == 'Image':
        print(name,key)
    name_list.add(name)
    

Image Rhode Island


In [119]:
len(state_museums_list)

47

In [ ]:
state_museum_list = []
with open('./data_1101/wikipedia_museum_list.jsonl','rt') as f:
    for line in f:
        state_museum_list.append(json.loads(line))

wikipedia_museum_articles = spider.wiki_artcle_filter(state_museum_list)

In [ ]:
#save articles
def wiki_save_articles(file_name:str,wiki_articles:list)->None:
    with open(file_name,'wt') as f:
        for museum in wiki_articles:
            f.write(json.dumps(museum)+'\n')

In [122]:
wiki_save_articles('./data_1101/wikipedia_museum_articles.jsonl',wikipedia_museum_articles)

In [11]:
# add the museums from embedded_links

embedded_links = [\
'https://en.wikipedia.org/wiki/List_of_museums_in_the_California_Central_Coast',\
'https://en.wikipedia.org/wiki/List_of_museums_in_the_Inland_Empire',\
'https://en.wikipedia.org/wiki/List_of_museums_in_Los_Angeles',\
'https://en.wikipedia.org/wiki/List_of_museums_in_the_North_Coast_(California)',\
'https://en.wikipedia.org/wiki/List_of_museums_in_Orange_County,_California',\
'https://en.wikipedia.org/wiki/List_of_museums_in_the_San_Francisco_Bay_Area',\
'https://en.wikipedia.org/wiki/List_of_museums_in_the_San_Joaquin_Valley',\
'https://en.wikipedia.org/wiki/List_of_museums_in_the_Shasta_Cascade',\
'https://en.wikipedia.org/wiki/List_of_museums_in_Atlanta',\
'https://en.wikipedia.org/wiki/List_of_museums_in_New_York_City',\
'https://en.wikipedia.org/wiki/List_of_museums_on_Long_Island',\
'https://en.wikipedia.org/wiki/List_of_museums_in_Philadelphia',\
'https://en.wikipedia.org/wiki/List_of_museums_in_Pittsburgh',\
'https://en.wikipedia.org/wiki/List_of_museums_in_Boston',\
'https://en.wikipedia.org/wiki/List_of_museums_in_Seattle',\
'https://en.wikipedia.org/wiki/List_of_museums_in_St._Louis',\
'https://en.wikipedia.org/wiki/List_of_museums_in_Kansas_City,_Missouri',\
]
state_name = ['California','California','California','California','California','California','California','California',\
              'Georgia','New York','New York','Pennsylvania','Pennsylvania','Massachusetts','Washington (state)','Missouri.','Missouri.']

In [ ]:
added_lists = {}
for idx,url in tqdm(enumerate(embedded_links),total=len(embedded_links)):
    single_state_museum_list = spider.get_single_state_museum_list(url)
    added_lists[state_name[idx]] = single_state_museum_list
    
spider.save_raw_list('./data_1101/wikipedia_added_list.jsonl',added_lists)

In [ ]:
added_lists = []
with open('./data_1101/wikipedia_added_list.jsonl','rt') as f:
    for line in f:
        added_lists.append(json.loads(line))

wiki_added_articles = spider.wiki_article_filter(added_lists)

In [ ]:
# merge added lists with the original

data0 = []
with open('./data_1101/wikipedia_museum_articles.jsonl','rt') as f: 
    for line in f:
        data0.append(json.loads(line))
f.close()

n_max = len(data0)
with open('./data_1101/wikipedia_museum_articles2.jsnol','wt') as f:
    for museum in data0:
        f.write(json.dumps(museum)+'\n')
    for museum in wiki_added_articles:
        museum['museum_id'] = n_max
        f.write(json.dumps(museum)+'\n')
        n_max +=1

In [2]:
# get inbox card info
museums_metadata = []
with open('./data_1101/wikipedia_museum_articles2.jsnol','rt') as f:
    for line in f:
        museums_metadata.append(json.loads(line))

In [15]:
museums_metadata

[{'museum_id': 0,
  'museum_name': 'Alabama Administrative Office of Courts Museum Area',
  'museum_url': 'https://en.wikipedia.org/wiki/Alabama_Judicial_Building',
  'wiki_article': "Heflin-Torbert Judicial Building, commonly called the Alabama Judicial Building, is a state government building in Montgomery, Alabama. It houses several state judicial agencies, most notably the Supreme Court of Alabama, Alabama Court of Civil Appeals, and Alabama Court of Criminal Appeals. It is the first state court building in the United States to house all three courts under one roof. Additionally, it houses the State Law Library.\nThe neoclassical-style structure was completed in 1994 at a cost of approximately $35 million.\nIn 2001, Roy Moore, who was Chief Justice at the time, placed a Ten Commandments monument on public display in the rotunda of the building. This placement of a religious monument in a government judicial building caused a nationwide controversy.\n\n\n== Architecture and features

In [3]:
spider = WikiSpider()
new_museums_metadata = spider.get_all_wiki_inbodx_info(museums_metadata)

100%|██████████| 5741/5741 [34:27<00:00,  2.78it/s]  


In [ ]:
new_museums_metadata2 = []

for idx,museum in tqdm(enumerate(new_museums_metadata),total = len(new_museums_metadata)):
        try:
            if (type(museum['Coordinates']) == str)and (len(museum["Coordinates"])>0):
                lat,log = re.findall(r"\d+\.\d*",museum["Coordinates"])
                lat = float(lat)
                log = -float(log)
                museum["Coordinates"] = (lat,log)
        except KeyError:
            pass
        
        new_museums_metadata2.append(museum)

In [26]:
with open('./data_1101/wikipedia_museum_articles3.jsnol','wt') as f:
        for museum in new_museums_metadata2:
                f.write(json.dumps(museum)+'\n')

## Web Crawling: which museum

In [21]:
from WMuseumSpider import WMuseumSpider
importlib.reload(sys.modules['WMuseumSpider'])

<module 'WMuseumSpider' from '/Users/leilei/Desktop/courses/si650/project/WMuseumSpider.py'>

In [22]:
spider = WMuseumSpider()
page_url ='https://whichmuseum.com/place/united-states-2682'
museums_urls=[]
start_page = 1
end_page = 1000

In [ ]:
# 834 pages are accessible
pages_museums_url = spider.get_pages_museums_url(page_url,museums_urls,1,834)

In [27]:
# save museum urls
with open('./data_1101/wmuseums_museum_urls.jsonl','wt') as f:
    for museum in pages_museums_url:
        output = {'museum_name':list(museum.keys())[0]}
        for item in museum.values():
            output.update(item)
        f.write(json.dumps(output)+'\n')

In [5]:
# read museum urls file
pages_museums_url = []
with open('./data_1101/wmuseums_museum_urls.jsonl','rt') as f:
    for line in f:
        pages_museums_url.append(json.loads(line))

In [23]:
wmuseum_museums_info = []
for museum in tqdm(pages_museums_url,total = len(pages_museums_url)):
# museum = pages_museums_url[0]
    single_museum_info = spider.get_single_museum_info(museum['wmuseum_link'])
    museum.update(single_museum_info)
    wmuseum_museums_info.append(museum)

100%|██████████| 9996/9996 [3:01:43<00:00,  1.09s/it]   


In [26]:
with open('./data_1101/which_museum_museum_info.jsonl','wt') as f:
    for museum in wmuseum_museums_info:
        f.write(json.dumps(museum)+'\n')

## ⚠️ invalid： Web Crawling: museum of the world

In [8]:
from invalid_files.WorldSpider import WorldSpider
import importlib
import sys
importlib.reload(sys.modules['WorldSpider'])



spider = WorldSpider()
page_url = 'https://museu.ms/search/index?documenttype=InstitutionUnit&countrycode=us&page='
museums_urls = []
start_page = 1

In [9]:
pages_museums_url = spider.get_pages_museums_url(page_url,museums_urls,start_page)

  5%|▌         | 50/1000 [00:18<05:56,  2.66it/s] 

current page {page} is empty
